Word Embeddings

1. average the vector for each single word in ImageNet list

In [4]:
%%time
from gensim.models import Word2Vec
from gensim.test.utils import common_texts
from gensim.models import Word2Vec
import gensim.downloader as api
import gensim

import pandas as pd
import numpy as np



CPU times: user 27 µs, sys: 1 µs, total: 28 µs
Wall time: 31.9 µs


In [5]:
%%time
#As model we use a pretrained model from FastText:
# https://fasttext.cc/docs/en/pretrained-vectors.html
# This model has 6gb of data DISCUSSION: Should we use it?
model = gensim.models.KeyedVectors.load_word2vec_format('wiki.en/wiki.en.vec', binary=False)

CPU times: user 6min 9s, sys: 8.49 s, total: 6min 17s
Wall time: 6min 23s


In [6]:
#word2vec_model’ parameter is the loaded word2vec model
#‘words’ parameter is a tokens list (strings) of the sentence / paragraph / document that you want to calculate
def get_mean_vector(word2vec_model, words):
    # remove out-of-vocabulary words
    words = [word for word in words if word in word2vec_model.key_to_index]
    if len(words) >= 1:
        return np.mean(word2vec_model[words], axis=0)
    else:
        return []

In [7]:
df_imgnet = pd.read_csv("../files/ImageNet.csv")
class_list = df_imgnet["Class Name"].tolist()

In [8]:
averaged_vectors = []
for el in class_list:
    vec = get_mean_vector(model, el)
    if len(vec) > 0:
      # do somthing with the vector ${vec}
      averaged_vectors.append(vec)

In [9]:
#TODO: Check if this is correct and how to find zero vectors.
averaged_vectors

[array([-0.11148707, -0.00407255,  0.04848633, -0.04510199, -0.10757219,
        -0.09543126,  0.076703  , -0.16729726, -0.04986733,  0.03299448,
         0.1649838 , -0.06670614,  0.012443  ,  0.06694046,  0.15077394,
        -0.3031976 , -0.18306626,  0.16398802, -0.00456473,  0.14829601,
         0.03024513,  0.05324926, -0.18696672, -0.36316252, -0.23964335,
         0.08525347,  0.04878133, -0.13991955, -0.10383221,  0.16280867,
         0.0221534 ,  0.32050163,  0.01605754,  0.00545263,  0.06581173,
        -0.0678768 , -0.03360683,  0.06770407,  0.1613506 , -0.13211195,
         0.03086908, -0.04548993, -0.03144873, -0.00444533,  0.0355138 ,
         0.12335862,  0.03180579, -0.0111402 ,  0.07054024, -0.08384454,
         0.00645082, -0.24766466,  0.03561031, -0.1304988 , -0.03944574,
         0.09049093,  0.00362157,  0.1517972 , -0.18632148,  0.28792715,
         0.03490354, -0.18463214,  0.26073638,  0.09120072, -0.048352  ,
        -0.09886904, -0.088778  , -0.21469043, -0.1

2. take zero vectors for words can not be vectorized. for example for hammerhead shark, hammerhead could be zero, but still /2 because two words

In [10]:
#TODO:

First Approach:
Take each item in the ImageNet list, prepare to each dbpedia Class and take the highest score

In [139]:
img_net = pd.read_csv("../files/ImageNet.csv")
img_net_list_str= img_net["Class Name"].tolist()
img_net['Class Name'] = img_net['Class Name'].str.replace(", ",",")
img_net['Class Name'] = img_net['Class Name'].str.split(",")
img_net_list = img_net["Class Name"].tolist()

dbpedia = pd.read_csv("../files/dbpedia_classes.csv")
db_list = dbpedia["label"].tolist()
sim_df = pd.DataFrame(index =db_list ,columns =img_net_list_str)
sim_df_avg = pd.DataFrame(index =db_list ,columns =img_net_list_str)



In [128]:
%%time
for el_img in img_net_list:
    for el_db in db_list:
        if len(el_db.split(" ")) > 1:
            new_el_db = []
            for e in el_db.split(" "):
                if model
                new_el_db.append()
        if len(el_img) == 1:
            try:
                sim = model.similarity("".join(el_img),el_db)
                sim_df.at[el_db,", ".join(el_img)] = sim
            except:
                sim_df.at[el_db,", ".join(el_img)] = "Not present"
        elif len(el_img) > 1:
            val = 0
            for el_array in el_img:  #we choose the entry with the highest value
                try:
                    sim = model.similarity(el_array,el_db)
                    if sim > val:
                        val = sim
                        sim_df.at[el_db,", ".join(el_img)] = val
                except:
                    pass
                
            if sim_df.at[el_db,", ".join(el_img)] is 0:
                sim_df.at[el_db,", ".join(el_img)] = "Not present"
                    

<timed exec>:20: SyntaxWarning: "is" with a literal. Did you mean "=="?


CPU times: user 5min 24s, sys: 1.27 s, total: 5min 25s
Wall time: 5min 26s


In [130]:
#replace all Not present with NaN
sim_df =sim_df.replace('Not present', np.nan) #I tried it with -2 before but nan is better way to go
sim_df

tench, Tinca tinca  goldfish, Carassius auratus  \
company               0.166713                     0.161003   
activity              0.150399                     0.167438   
name                  0.162085                     0.149808   
person                0.156646                     0.236590   
actor                 0.239988                     0.176655   
...                        ...                          ...   
Wind motor                 NaN                          NaN   
Windmill                   NaN                          NaN   
wine                  0.164880                     0.200409   
woman                 0.127441                     0.199175   
zoo                   0.152080                     0.360922   

            great white shark, white shark, man-eater, man-eating shark, Carcharodon caharias',  \
company                                                   NaN                                     
activity                                                  NaN                                     
name                                                      NaN                                     
person                                                    NaN                                     
actor                                                     NaN                                     
...                                                       ...                                     
Wind motor                                                NaN                                     
Windmill                                                  NaN                                     
wine                                                      NaN                                     
woman                                                     NaN                                     
zoo                                                       NaN                                     

            tiger shark, Galeocerdo cuvieri  hammerhead, hammerhead shark  \
company                                 NaN                      0.145090   
activity                                NaN                      0.232189   
name                                    NaN                      0.114972   
person                                  NaN                      0.169407   
actor                                   NaN                      0.117483   
...                                     ...                           ...   
Wind motor                              NaN                           NaN   
Windmill                                NaN                           NaN   
wine                                    NaN                      0.062539   
woman                                   NaN                      0.181474   
zoo                                     NaN                      0.257263   

            electric ray, crampfish, numbfish, torpedo  stingray      cock  \
company                                       0.234623  0.198235  0.136673   
activity                                      0.128309  0.095837  0.118225   
name                                          0.131952  0.139868  0.230916   
person                                        0.172420  0.132319  0.205509   
actor                                         0.200618  0.125034  0.180400   
...                                                ...       ...       ...   
Wind motor                                         NaN       NaN       NaN   
Windmill                                           NaN       NaN       NaN   
wine                                          0.216428  0.149223  0.133900   
woman                                         0.189917  0.133640  0.240082   
zoo                                           0.218953  0.225380  0.253591   

                 hen  ostrich, Struthio camelus  ...  \
company     0.108277                   0.151611  ...   
activity    0.116898                   0.164307  ...   
name        0.168908                

Now we get the highest value of each column and index and drop all values that are not available.

In [131]:
df = sim_df
max_df = df.idxmax()
cleaned_max_df = max_df.dropna()
max_val = pd.DataFrame(cleaned_max_df, columns=["Dbpedia"])

In [132]:
#this gives us all values of imagenet classes that are available
max_val_list = []
for el in cleaned_max_df.index:
    max_val_list.append(df[el].max())
max_val["Similarity"] = max_val_list

In [160]:
model.similarity('streetcar', 'streetcar')

1.0

In [159]:
max_val = max_val.sort_values(by='Similarity', ascending=False)
max_val.index.name = "ImageNet"
max_val.head(50)

Dbpedia  Similarity
ImageNet                                                                  
mosque                                                  mosque    1.000000
monastery                                            monastery    1.000000
organ, pipe organ                                        organ    1.000000
prison, prison house                                    prison    1.000000
file, file cabinet, filing cabinet                        file    1.000000
boxer                                                    boxer    1.000000
monarch, monarch butterfly, milkweed butterfly,...     monarch    1.000000
amphibian, amphibious vehicle                        amphibian    1.000000
castle                                                  castle    1.000000
library                                                library    1.000000
volcano                                                volcano    1.000000
church, church building                                 church    1.000000
restaurant, eating house, eating place, eatery      restaurant    0.894419
web site, website, internet site, site                 website    0.798405
airliner                                              aircraft    0.775980
isopod                                              crustacean    0.771061
streetcar, tram, tramcar, trolley, trolley car       streetcar    0.749380
bolete                                                  fungus    0.743190
accordion, piano accordion, squeeze box                 guitar    0.732460
ski                                                      skier    0.729278
banjo                                                   guitar    0.728411
crane, bird                                               bird    0.726295
agaric                                                  fungus    0.726227
obelisk                                               monument    0.716219
cricket                                              cricketer    0.713243
valley, vale                                            valley    0.709035
mushroom                                                fungus    0.690961
schooner                                                  ship    0.688167
moped                                               motorcycle    0.685554
viaduct                                                 bridge    0.683538
warplane, military plane                              aircraft    0.681636
leafhopper                                              insect    0.679539
tarantula                                             arachnid    0.675178
dam, dike, dyke                                           dike    0.674029
harmonica, mouth organ, harp, mouth harp                guitar    0.661015
trombone                                                guitar    0.660406
flatworm, platyhelminth                             crustacean    0.651376
cheeseburger                                            cheese    0.651236
pizza, pizza pie                                    restaurant    0.647935
violin, fiddle                                          guitar    0.647386
racer, race car, racing car                            cyclist    0.644849
missile                                                 rocket    0.644192
goldfish, Carassius auratus                               fish    0.643861
dough                                                   cheese    0.640569
sax, saxophone                                          guitar    0.635375
passenger car, coach, carriage                           coach    0.632187
trilobite                                           crustacean    0.631796
projectile, missile                                     weapon    0.631368
eel                                                       fish    0.630069
nematode, nematode worm, roundworm                      insect    0.626034

In [135]:
len(max_val)

798

Second Approach: Average the vector of the items in imageNet class.
In the End we gotTwo sets of results. 
Write a function for top three matchings of dbpedia_class

In [150]:
for el_img in img_net_list:
    for el_db in db_list:
        if len(el_img) == 1:
            try:
                sim = model.similarity("".join(el_img),el_db)
                sim_df_avg.at[el_db,", ".join(el_img)] = sim
            except:
                sim_df_avg.at[el_db,", ".join(el_img)] = "Not present"
        elif len(el_img) > 1:
            val = []
            sim_df_avg.at[el_db,", ".join(el_img)]=0
            for el_array in el_img:  #we choose the entry with the highest value
                try:
                    sim = model.similarity(el_array,el_db)
                    val.append(sim)
                except:
                    pass
            if val:
                sim_df_avg.at[el_db,", ".join(el_img)] = np.mean(val)
   
            if sim_df_avg.at[el_db,", ".join(el_img)] is 0:
                sim_df_avg.at[el_db,", ".join(el_img)] = "Not present"

<>:22: SyntaxWarning: "is" with a literal. Did you mean "=="?
<>:22: SyntaxWarning: "is" with a literal. Did you mean "=="?
/var/folders/rl/bmzv82250753s6nrlbm67tm40000gn/T/ipykernel_4316/3461239304.py:22: SyntaxWarning: "is" with a literal. Did you mean "=="?
  if sim_df_avg.at[el_db,", ".join(el_img)] is 0:


In [151]:
sim_df_avg

tench, Tinca tinca goldfish, Carassius auratus  \
company              0.166713                    0.161003   
activity             0.150399                    0.167438   
name                 0.162085                    0.149808   
person               0.156646                     0.23659   
actor                0.239988                    0.176655   
...                       ...                         ...   
Wind motor        Not present                 Not present   
Windmill          Not present                 Not present   
wine                  0.16488                    0.200409   
woman                0.127441                    0.199175   
zoo                   0.15208                    0.360922   

           great white shark, white shark, man-eater, man-eating shark, Carcharodon caharias',  \
company                                                   NaN                                    
activity                                                  NaN                                    
name                                                      NaN                                    
person                                                    NaN                                    
actor                                                     NaN                                    
...                                                       ...                                    
Wind motor                                                NaN                                    
Windmill                                                  NaN                                    
wine                                                      NaN                                    
woman                                                     NaN                                    
zoo                                                       NaN                                    

           tiger shark, Galeocerdo cuvieri hammerhead, hammerhead shark  \
company                        Not present                      0.14509   
activity                       Not present                     0.232189   
name                           Not present                     0.114972   
person                         Not present                     0.169407   
actor                          Not present                     0.117483   
...                                    ...                          ...   
Wind motor                     Not present                  Not present   
Windmill                       Not present                  Not present   
wine                           Not present                     0.062539   
woman                          Not present                     0.181474   
zoo                            Not present                     0.257263   

           electric ray, crampfish, numbfish, torpedo     stingray  \
company                                      0.182702     0.198235   
activity                                     0.119412     0.095837   
name                                         0.117525     0.139868   
person                                       0.151225     0.132319   
actor                                        0.170048     0.125034   
...                                               ...          ...   
Wind motor                                Not present  Not present   
Windmill                                  Not present  Not present   
wine                                         0.162778     0.149223   
woman                                        0.149341      0.13364   
zoo                                          0.161961      0.22538   

                   cock          hen ostrich, Struthio camelus  ...  \
company        0.136673     0.108277                  0.151611  ...   
activity       0.118225     0.116898                  0.164307  ...   
name           0.230916     0.168908                  0.169268  ...   
person         0.205509     0.177245                  0.148699  ...   
acto

In [158]:
sim_df_avg =sim_df_avg.replace('Not present', np.nan) #I tried it with -2 before but nan is better way to go
df = sim_df_avg
max_df = df.idxmax()
cleaned_max_df = max_df.dropna()
max_val = pd.DataFrame(cleaned_max_df, columns=["Dbpedia"])
#this gives us all values of imagenet classes that are available
max_val_list = []
for el in cleaned_max_df.index:
    max_val_list.append(df[el].max())
max_val["Similarity"] = max_val_list
max_val = max_val.sort_values(by='Similarity', ascending=False)
max_val.index.name = "ImageNet"
max_val.head(50)

Dbpedia  Similarity
ImageNet                                                                  
mosque                                                  mosque    1.000000
monastery                                            monastery    1.000000
organ, pipe organ                                        organ    1.000000
prison, prison house                                    prison    1.000000
file, file cabinet, filing cabinet                        file    1.000000
boxer                                                    boxer    1.000000
monarch, monarch butterfly, milkweed butterfly,...     monarch    1.000000
amphibian, amphibious vehicle                        amphibian    1.000000
castle                                                  castle    1.000000
library                                                library    1.000000
volcano                                                volcano    1.000000
church, church building                                 church    1.000000
restaurant, eating house, eating place, eatery      restaurant    0.894419
web site, website, internet site, site                 website    0.798405
airliner                                              aircraft    0.775980
isopod                                              crustacean    0.771061
streetcar, tram, tramcar, trolley, trolley car       streetcar    0.749380
bolete                                                  fungus    0.743190
accordion, piano accordion, squeeze box                 guitar    0.732460
ski                                                      skier    0.729278
banjo                                                   guitar    0.728411
crane, bird                                               bird    0.726295
agaric                                                  fungus    0.726227
obelisk                                               monument    0.716219
cricket                                              cricketer    0.713243
valley, vale                                            valley    0.709035
mushroom                                                fungus    0.690961
schooner                                                  ship    0.688167
moped                                               motorcycle    0.685554
viaduct                                                 bridge    0.683538
warplane, military plane                              aircraft    0.681636
leafhopper                                              insect    0.679539
tarantula                                             arachnid    0.675178
dam, dike, dyke                                           dike    0.674029
harmonica, mouth organ, harp, mouth harp                guitar    0.661015
trombone                                                guitar    0.660406
flatworm, platyhelminth                             crustacean    0.651376
cheeseburger                                            cheese    0.651236
pizza, pizza pie                                    restaurant    0.647935
violin, fiddle                                          guitar    0.647386
racer, race car, racing car                            cyclist    0.644849
missile                                                 rocket    0.644192
goldfish, Carassius auratus                               fish    0.643861
dough                                                   cheese    0.640569
sax, saxophone                                          guitar    0.635375
passenger car, coach, carriage                           coach    0.632187
trilobite                                           crustacean    0.631796
projectile, missile                                     weapon    0.631368
eel                                                       fish    0.630069
nematode, nematode worm, roundworm                      insect    0.626034